In [1]:
import os
import pandas as pd
import numpy as np
import sys
import copy
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [2]:
self = SignalGenerator()
self.prepare_data() # 1 
self.process_history() # 2
self.process_movement() # 3
self.make_histids() # 4
self.set_timepoints() # 5-1
self.assign_red_yellow() # 5-2

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.


In [3]:
print(self.parent_ids)
print(self.uturn_ids)
print(self.coord_ids)

['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']
['u00', 'u20', 'u30', 'u31', 'u32', 'u60']
['c30']


In [4]:
node_id = self.parent_ids[0]
self.SIGTABLE[self.SIGTABLE.node_id==node_id]

node_id  start_unix  phase  duration              state
0       i0  1704418330  1g_1g        39  gGGrgrrrgGGGGrgrr
1       i0  1704418330  1y_1y         4  gyyrgrrrgyyyyrgrr
2       i0  1704418330  2r_2r         1  grrrgrrrgrrrrrgrr
3       i0  1704418330  2g_2g        40  grrGgrrrgrrrrGgrr
4       i0  1704418330  2y_2y         4  grrygrrrgrrrrygrr
5       i0  1704418330  3r_3r         1  grrrgGGrgrrrrrgrr
6       i0  1704418330  3g_3g        28  grrrgGGGgrrrrrgrr
7       i0  1704418330  3g_3y         4  grrrgGGygrrrrrgrr
8       i0  1704418330  3g_4r         1  grrrgGGrgrrrrrgGr
9       i0  1704418330  3g_4g        17  grrrgGGrgrrrrrgGr
10      i0  1704418330  3y_4g         4  grrrgyyrgrrrrrgGr
11      i0  1704418330  4r_4g         1  grrrgrrrgrrrrrgGr
12      i0  1704418330  4g_4g        32  grrrgrrrgrrrrrgGG
13      i0  1704418330  4y_4y         4  grrrgrrrgrrrrrgyy
14      i0  1704418510  1r_1r         1  grrrgrrrgrrrrrgrr
15      i0  1704418510  1g_1g        38  gGGrgrrrgGGGGrgrr
16      i0  1704418510  1y_1y         4  gyyrgrrrgyyyyrgrr
17      i0  1704418510  2r_2r         1  grrrgrrrgrrrrrgrr
18      i0  1704418510  2g_2g        40  grrGgrrrgrrrrGgrr
19      i0  1704418510  2y_2y         4  grrygrrrgrrrrygrr
20      i0  1704418510  3r_3r         1  grrrgGGrgrrrrrgrr
21      i0  1704418510  3g_3g        28  grrrgGGGgrrrrrgrr
22      i0  1704418510  3g_3y         4  grrrgGGygrrrrrgrr
23      i0  1704418510  3g_4r         1  grrrgGGrgrrrrrgGr
24      i0  1704418510  3g_4g        17  grrrgGGrgrrrrrgGr
25      i0  1704418510  3y_4g         4  grrrgyyrgrrrrrgGr
26      i0  1704418510  4r_4g         1  grrrgrrrgrrrrrgGr
27      i0  1704418510  4g_4g        32  grrrgrrrgrrrrrgGG
28      i0  1704418510  4y_4y         4  grrrgrrrgrrrrrgyy
29      i0  1704418690  1r_1r         1  grrrgrrrgrrrrrgrr
30      i0  1704418690  1g_1g        38  gGGrgrrrgGGGGrgrr
31      i0  1704418690  1y_1y         4  gyyrgrrrgyyyyrgrr
32      i0  1704418690  2r_2r         1  grrrgrrrgrrrrrgrr
33      i0  1704418690  2g_2g        40  grrGgrrrgrrrrGgrr
34      i0  1704418690  2y_2y         4  grrygrrrgrrrrygrr
35      i0  1704418690  3r_3r         1  grrrgGGrgrrrrrgrr
36      i0  1704418690  3g_3g        28  grrrgGGGgrrrrrgrr
37      i0  1704418690  3g_3y        22  grrrgGGygrrrrrgrr

In [8]:
self = SignalGenerator()
self.prepare_data() # 1 
self.process_history() # 2
self.process_movement() # 3
self.make_histids() # 4
self.set_timepoints() # 5-1

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.


In [14]:
NODE_ID = 'i7'
sigtable = self.sigtable[self.sigtable.node_id==NODE_ID]
display(sigtable)

self.SIGTABLE = []
for node_id in self.node_ids:
    sig = self.sigtable.query('node_id==@node_id')
    for i, row in sig.iterrows():
        inter_no = row.inter_no
        phas_A = row.phas_A
        phas_B = row.phas_B
        start_unix = row.start_unix
        prow = self.load_prow(inter_no, start_unix)[1].iloc[0]
        red_A    = prow[f'red_A{phas_A}']
        yellow_A = prow[f'yellow_A{phas_A}']
        red_B    = prow[f'red_B{phas_B}']
        yellow_B = prow[f'yellow_B{phas_B}']
        sig.loc[i, ['red_A', 'red_B', 'yellow_A', 'yellow_B']] = red_A, red_B, yellow_A, yellow_B
    sig = sig.astype({'red_A': int, 'red_B': int, 'yellow_A': int, 'yellow_B': int,
                    'phas_A':str, 'phas_B':str})
    sig = sig.drop(['move_A','move_B'], axis=1)

    sig_A = sig[['start_unix', 'phas_A', 'duration', 'state_A', 'red_A', 'yellow_A']].reset_index(drop=True)
    sig_B = sig[['start_unix', 'phas_B', 'duration', 'state_B', 'red_B', 'yellow_B']].reset_index(drop=True)

    csig_A = self.cumulate(sig_A, 'A')
    csig_B = self.cumulate(sig_B, 'B')

    SIG = pd.merge(csig_A, csig_B, on=['start_time', 'start_unix'], how='outer')
    SIG = SIG.sort_values(by='start_time').reset_index(drop=True)
    SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
    SIG[['phas_B', 'state_B']] = SIG[['phas_B', 'state_B']].fillna(method='ffill')
    SIG['phase'] = SIG['phas_A'] + "_" + SIG['phas_B']
    SIG['node_id'] = node_id
    SIG = SIG[['node_id', 'start_unix', 'start_time', 'phase', 'state_A', 'state_B']]
    SIG['duration'] = SIG['start_time'].shift(-1) - SIG['start_time']
    SIG = SIG[:-1]
    SIG['duration'] = SIG['duration'].astype(int)
    for row in SIG.itertuples():
        state = ''
        for a, b, in zip(row.state_A, row.state_B):
            if a == 'r':
                state += b
            elif b == 'r':
                state += a
            elif a == b:
                state += a
            else:
                raise ValueError(f"예상되지 않은 조합 발생: a={a}, b={b}")
        SIG.at[row.Index, 'state'] = state
    SIG = SIG.drop(columns=['start_time', 'state_A', 'state_B'])
    self.SIGTABLE.append(SIG)
self.SIGTABLE = pd.concat(self.SIGTABLE)

SIGTABLE = self.SIGTABLE[self.SIGTABLE.node_id==NODE_ID]
display(SIGTABLE)

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
86        206      i7  1704418700       1       1       8       4        45   
87        206      i7  1704418700       2       2      17      18        53   
88        206      i7  1704418700       3       3       8       4        26   
89        206      i7  1704418700       4       4      17      18        26   
90        206      i7  1704418850       1       1       8       4        45   
91        206      i7  1704418850       2       2      17      18        53   
92        206      i7  1704418850       3       3       8       4        26   
93        206      i7  1704418850       4       4      17      18        26   
94        206      i7  1704419000       1       1       8       4        45   
95        206      i7  1704419000       2       2      17      18        53   
96        206      i7  1704419000       3       3       8       4        26   
97        206      i7  1704419000       4       4      17      18        26   
98        206      i7  1704419150       1       1       8       4        45   
99        206      i7  1704419150       2       2      17      18        53   
100       206      i7  1704419150       3       3       8       4        26   
101       206      i7  1704419150       4       4      17      18        26   

     state_A  state_B  phase_sumo  
86   rrrggGG  GGrggrr           0  
87   rrrggrr  rrrggrr           1  
88   rrrggGG  GGrggrr           2  
89   rrrggrr  rrrggrr           3  
90   rrrggGG  GGrggrr           0  
91   rrrggrr  rrrggrr           1  
92   rrrggGG  GGrggrr           2  
93   rrrggrr  rrrggrr           3  
94   rrrggGG  GGrggrr           0  
95   rrrggrr  rrrggrr           1  
96   rrrggGG  GGrggrr           2  
97   rrrggrr  rrrggrr           3  
98   rrrggGG  GGrggrr           0  
99   rrrggrr  rrrggrr           1  
100  rrrggGG  GGrggrr           2  
101  rrrggrr  rrrggrr           3

node_id  start_unix  phase  duration    state
0       i7  1704418700  1g_1g        41  GGrggGG
1       i7  1704418700  1y_1y         4  yyrggyy
2       i7  1704418700  2r_2r         0  rrrggrr
3       i7  1704418700  2r_2g         0  rrrggrr
4       i7  1704418700  2g_2r         0  rrrggrr
..     ...         ...    ...       ...      ...
66      i7  1704419150  2y_2y         4  rrrggrr
67      i7  1704419150  3g_3r         0  rrrggGG
68      i7  1704419150  3g_3g         0  GGrggGG
69      i7  1704419150  3r_3r         0  rrrggrr
70      i7  1704419150  3r_3g        22  GGrggrr

[71 rows x 5 columns]

In [47]:
NODE_ID = 'i7'
sig = self.sigtable[self.sigtable.node_id==NODE_ID]
# display(sig.head())

for i, row in sig.iterrows():
    inter_no = row.inter_no
    phas_A = row.phas_A
    phas_B = row.phas_B
    start_unix = row.start_unix
    prow = self.load_prow(inter_no, start_unix)[1].iloc[0]
    red_A    = prow[f'red_A{phas_A}']
    yellow_A = prow[f'yellow_A{phas_A}']
    red_B    = prow[f'red_B{phas_B}']
    yellow_B = prow[f'yellow_B{phas_B}']
    sig.loc[i, ['red_A', 'red_B', 'yellow_A', 'yellow_B']] = red_A, red_B, yellow_A, yellow_B

sig = sig.astype({'red_A': int, 'red_B': int, 'yellow_A': int, 'yellow_B': int,
                'phas_A':str, 'phas_B':str})
sig = sig.drop(['move_A','move_B'], axis=1)

# display(sig.head())
sig_A = sig[['start_unix', 'phas_A', 'duration', 'state_A', 'red_A', 'yellow_A']].reset_index(drop=True)
sig_B = sig[['start_unix', 'phas_B', 'duration', 'state_B', 'red_B', 'yellow_B']].reset_index(drop=True)

display(sig_A.head())
display(sig_B.head())

csig_A = self.cumulate(sig_A, 'A')
csig_B = self.cumulate(sig_B, 'B')

display(csig_A.head())
display(csig_B.head())
SIG = pd.merge(csig_A, csig_B, on=['start_time', 'start_unix'], how='outer')
SIG = SIG.sort_values(by='start_time').reset_index(drop=True)
SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
SIG[['phas_B', 'state_B']] = SIG[['phas_B', 'state_B']].fillna(method='ffill')
SIG['phase'] = SIG['phas_A'] + "_" + SIG['phas_B']
SIG['node_id'] = node_id
SIG = SIG[['node_id', 'start_unix', 'start_time', 'phase', 'state_A', 'state_B']]
SIG['duration'] = SIG['start_time'].shift(-1) - SIG['start_time']
SIG = SIG[:-1]
SIG['duration'] = SIG['duration'].astype(int)
for row in SIG.itertuples():
    state = ''
    for a, b, in zip(row.state_A, row.state_B):
        if a == 'r':
            state += b
        elif b == 'r':
            state += a
        elif a == b:
            state += a
        else:
            raise ValueError(f"예상되지 않은 조합 발생: a={a}, b={b}")
    SIG.at[row.Index, 'state'] = state
SIG = SIG.drop(columns=['start_time', 'state_A', 'state_B'])

display(SIG.head())

start_unix phas_A  duration  state_A  red_A  yellow_A
0  1704418700      1        45  rrrggGG      0         4
1  1704418700      2        53  rrrggrr      0         4
2  1704418700      3        26  rrrggGG      0         4
3  1704418700      4        26  rrrggrr      0         4
4  1704418850      1        45  rrrggGG      0         4

start_unix phas_B  duration  state_B  red_B  yellow_B
0  1704418700      1        45  GGrggrr      0         4
1  1704418700      2        53  rrrggrr      0         4
2  1704418700      3        26  GGrggrr      0         4
3  1704418700      4        26  rrrggrr      0         4
4  1704418850      1        45  GGrggrr      0         4

start_time phas_A  state_A  start_unix
0           0     1g  rrrggGG  1704418700
1          41     1y  rrrggyy  1704418700
2          45     2r  rrrggrr  1704418700
3          45     2g  rrrggrr  1704418700
4          94     2y  rrrggrr  1704418700

start_time phas_B  state_B  start_unix
0           0     1g  GGrggrr  1704418700
1          41     1y  yyrggrr  1704418700
2          45     2r  rrrggrr  1704418700
3          45     2g  rrrggrr  1704418700
4          94     2y  rrrggrr  1704418700

node_id  start_unix  phase  duration    state
0     u60  1704418700  1g_1g        41  GGrggGG
1     u60  1704418700  1y_1y         4  yyrggyy
2     u60  1704418700  2r_2r         0  rrrggrr
3     u60  1704418700  2r_2g         0  rrrggrr
4     u60  1704418700  2g_2r         0  rrrggrr

In [50]:
display(SIG.head(10))
display(SIG[SIG.duration!=0].head(10))

node_id  start_unix  phase  duration    state
0     u60  1704418700  1g_1g        41  GGrggGG
1     u60  1704418700  1y_1y         4  yyrggyy
2     u60  1704418700  2r_2r         0  rrrggrr
3     u60  1704418700  2r_2g         0  rrrggrr
4     u60  1704418700  2g_2r         0  rrrggrr
5     u60  1704418700  2g_2g        49  rrrggrr
6     u60  1704418700  2y_2y         4  rrrggrr
7     u60  1704418700  3r_3r         0  rrrggrr
8     u60  1704418700  3r_3g         0  GGrggrr
9     u60  1704418700  3g_3r         0  rrrggGG

node_id  start_unix  phase  duration    state
0      u60  1704418700  1g_1g        41  GGrggGG
1      u60  1704418700  1y_1y         4  yyrggyy
5      u60  1704418700  2g_2g        49  rrrggrr
6      u60  1704418700  2y_2y         4  rrrggrr
10     u60  1704418700  3g_3g        22  GGrggGG
11     u60  1704418700  3y_3y         4  yyrggyy
15     u60  1704418700  4g_4g        22  rrrggrr
16     u60  1704418700  4y_4y         4  rrrggrr
20     u60  1704418850  1g_1g        41  GGrggGG
21     u60  1704418850  1y_1y         4  yyrggyy

In [53]:
reds = [f'red_{alph}{i}' for alph in ['A','B'] for i in range(1,9)]
yels = [f'yellow_{alph}{i}' for alph in ['A','B'] for i in range(1,9)]

In [62]:
zeros = (self.plan[reds + yels]==0)
self.plan[zeros.any(axis=1)]

inter_no  start_hour  start_minute  dura_A1  dura_A2  dura_A3  dura_A4  \
24       206           0             0       33       35       26       26   
25       206           7             0       44       44       26       26   
26       206           9             0       45       53       26       26   
27       206          18            30       46       62       26       26   

    dura_A5  dura_A6  dura_A7  ...  red_A4  red_B4  red_A5  red_B5  red_A6  \
24        0        0        0  ...       0       0       0       0       0   
25        0        0        0  ...       0       0       0       0       0   
26        0        0        0  ...       0       0       0       0       0   
27        0        0        0  ...       0       0       0       0       0   

    red_B6  red_A7  red_B7  red_A8  red_B8  
24       0       0       0       0       0  
25       0       0       0       0       0  
26       0       0       0       0       0  
27       0       0       0       0       0  

[4 rows x 53 columns]